In [5]:
import pandas as pd
import scipy.io as sio
from scipy import signal, stats
import numpy as np
import datetime
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import re
from scipy import signal
from scipy import integrate
from oceans.filters import lanc

predictedSMidDF = pd.read_csv('surface_temperature_model_mid12-13.csv', parse_dates = ["DN"])
predictedBMidDF = pd.read_csv('bottom_temperature_model_mid12-13.csv', parse_dates = ["DN"])
heatMidDF = pd.read_csv('mid_heatflux_2012-2013.csv', parse_dates = ['Tm (UTC)'])
heatMidDF = pd.merge_asof(predictedSMidDF, heatMidDF, left_on="DN", right_on = "Tm (UTC)")[["Qnet"]]
riverDF = pd.read_csv('river_temperature_interpol12_13.csv', parse_dates = ['DN'])
riverDF = pd.merge_asof(predictedSMidDF, riverDF, left_on="DN", right_on = "DN" )[["EstimatedTemp"]]

#BUTTERWORTH FILTER METHOD
fs = 12*36  # Sampling frequency
fcHighpass = 24/36  # Cut-off frequency of the filter
wHighpass = fcHighpass / (fs / 2) # Normalize the frequency
#fcLowpass = 24/6  # Cut-off frequency of the filter
#wLowpass = fcLowpass / (fs / 2) # Normalize the frequency
surfaceDF = pd.DataFrame({'T' : predictedSMidDF["TempDiff"]})
bottomDF = pd.DataFrame({'T' : predictedBMidDF["TempDiff"]})
heatDF = pd.DataFrame({'T' : heatMidDF["Qnet"]})
# interp fills Nan's within and bfill, ffill fills nans that are located before data starts and after data
surfaceAdjustedTemp = surfaceDF['T'].interpolate().bfill().ffill().to_numpy()
bottomAdjustedTemp = bottomDF['T'].interpolate().bfill().ffill().to_numpy()
heatAdjusted = heatDF['T'].interpolate().bfill().ffill().to_numpy()
#sosHighpass = signal.butter(10, wHighpass, 'highpass', analog = False, output = 'sos')
surfaceLowpass = signal.butter(4, wHighpass, 'lowpass', analog = False, output = 'sos')
bottomLowpass = signal.butter(4, wHighpass, 'lowpass', analog = False, output = 'sos')
heatLowpass = signal.butter(4, wHighpass, 'lowpass', analog = False, output = 'sos')
#outputHigh = signal.sosfilt(sosHighpass, testTemp)
outputSurfaceLow = signal.sosfiltfilt(surfaceLowpass, surfaceAdjustedTemp)
outputSurfaceHigh = outputSurfaceLow - predictedSMidDF['TempDiff']
outputBottomLow = signal.sosfiltfilt(bottomLowpass, bottomAdjustedTemp)
outputHeatLow = signal.sosfiltfilt(heatLowpass, heatAdjusted)
#hipass heatflux: Qnet - outputHeatLow

#low frequency adjusted for mean
outputHeatLowAdjusted = outputHeatLow - min(outputHeatLow)
outputHeatHigh = heatMidDF["Qnet"] - outputHeatLow

#dT/dt = Qnet / po * Cp * H
#where 1025 kg/m3 = po, Cp = 4010 J/(kg °C), H = 2.5 m
heatModelHigh = outputHeatHigh/(1025 * 4010 * 2.5)
heatModelLow = outputHeatLowAdjusted/(1025 * 4010 * 2.5)

integratedHighModel = integrate.cumulative_trapezoid(heatModelHigh, initial = 0)
integratedLowModel = integrate.cumulative_trapezoid(heatModelLow, initial = 0)
'''
figLabels = ["Integrated High Pass Heat", "Integrated Low Pass Heat", "Temp Diff"]
fig1 = px.line(x= predictedSMidDF['DN'], y = [integratedHighModel, integratedLowModel], color_discrete_sequence = ["gray", "royalblue"])
fig2 = px.line(x=predictedSMidDF['DN'], y= [outputSurfaceLow], color_discrete_sequence = ["green"])

# Create subplots with secondary y-axis
fig = make_subplots(specs=[[{"secondary_y": True}]])
# Add traces to subplots
fig.add_trace(fig1.data[0], secondary_y=False)
fig.add_trace(fig1.data[1], secondary_y=False)
fig.add_trace(fig2.data[0], secondary_y=True)
for idx in range(len(figLabels)):
    fig.data[idx].name = figLabels[idx]
    fig.data[idx].hovertemplate = 'variable=' + figLabels[idx] + '<br>x=%{x}<br>value=%{y}<extra></extra>'
    fig.data[idx].legendgroup = figLabels[idx]
fig.update_yaxes(showline=True, linewidth=2, linecolor='black', zeroline=True, zerolinewidth=2, zerolinecolor="black", gridcolor = 'white')
fig.update_xaxes(gridcolor = 'white')
fig.update_layout(paper_bgcolor='white', plot_bgcolor='white')
fig.update_layout(
    title_text="Temperature and Heat Flux 2013",
    xaxis_title="Date",
    yaxis_title="Temperature (°C)",
    yaxis2_title="Temperature (°C)",
)

fig.show()
'''
fig2Labels = ["Integrated Low Pass Heat", "Low pass Temp Diff"]
fig21 = px.line(x= predictedSMidDF['DN'], y = [integratedLowModel], color_discrete_sequence = ["royalblue"])
fig22 = px.line(x=predictedSMidDF['DN'], y= [outputSurfaceLow], color_discrete_sequence = ["green"])

# Create subplots with secondary y-axis
fig2 = make_subplots(specs=[[{"secondary_y": True}]])
# Add traces to subplots
fig2.add_trace(fig21.data[0], secondary_y=False)
fig2.add_trace(fig22.data[0], secondary_y=True)
for idx in range(len(fig2Labels)):
    fig2.data[idx].name = fig2Labels[idx]
    fig2.data[idx].hovertemplate = 'variable=' + fig2Labels[idx] + '<br>x=%{x}<br>value=%{y}<extra></extra>'
    fig2.data[idx].legendgroup = fig2Labels[idx]
fig2.update_yaxes(showline=True, linewidth=2, linecolor='black', zeroline=True, zerolinewidth=2, zerolinecolor="black", gridcolor = 'white')
fig2.update_xaxes(gridcolor = 'white')
fig2.update_layout(paper_bgcolor='white', plot_bgcolor='white')
fig2.update_layout(
    title_text="Low Pass Comparison 2013",
    xaxis_title="Date",
    yaxis_title="Temperature (°C)",
    yaxis2_title="Temperature (°C)",
)

fig2.show()

fig3Labels = ["Integrated High Pass Heat", "High Pass Temp Diff"]
fig31 = px.line(x= predictedSMidDF['DN'], y = [integratedHighModel], color_discrete_sequence = ["gray"])
fig32 = px.line(x=predictedSMidDF['DN'], y= [outputSurfaceHigh], color_discrete_sequence = ["green"])

# Create subplots with secondary y-axis
fig3 = make_subplots(specs=[[{"secondary_y": True}]])
# Add traces to subplots
fig3.add_trace(fig31.data[0], secondary_y=False)
fig3.add_trace(fig32.data[0], secondary_y=True)
for idx in range(len(fig3Labels)):
    fig3.data[idx].name = fig3Labels[idx]
    fig3.data[idx].hovertemplate = 'variable=' + fig3Labels[idx] + '<br>x=%{x}<br>value=%{y}<extra></extra>'
    fig3.data[idx].legendgroup = fig3Labels[idx]
fig3.update_yaxes(showline=True, linewidth=2, linecolor='black', zeroline=True, zerolinewidth=2, zerolinecolor="black", gridcolor = 'white')
fig3.update_xaxes(gridcolor = 'white')
fig3.update_layout(paper_bgcolor='white', plot_bgcolor='white')
fig3.update_layout(
    title_text="HighPass Comparison 2013",
    xaxis_title="Date",
    yaxis_title="Temperature (°C)",
    yaxis2_title="Temperature (°C)",
)

fig3.show()




'''
tempFigLabels = ['Surface', 'Predicted', 'Difference', 'Difference Lowpass', 'River Temperature']
tempfig = px.line(x = predictedSMidDF['DN'], y = [predictedSMidDF['OriginalTemp'], predictedSMidDF["ModelTemp"], predictedSMidDF['TempDiff'], outputSurfaceLow, riverDF['EstimatedTemp']], color_discrete_sequence= ["black", "blue", "orange", "red", "green"], title = "Temperature")
for idx in range(len(tempFigLabels)):
    tempfig.data[idx].name = tempFigLabels[idx]
    tempfig.data[idx].hovertemplate = 'variable=' + tempFigLabels[idx] + '<br>x=%{x}<br>value=%{y}<extra></extra>'
    tempfig.data[idx].legendgroup = tempFigLabels[idx]

tempfig.update_layout(title=dict(text= "Surface Temperature Midestuary for 2013", font=dict(size=25)))
tempfig.update_xaxes(tickangle=30)
tempfig.update_xaxes(rangeslider_visible=True)
tempfig.update_xaxes(range = [pd.Timestamp('2013-01-21'),pd.Timestamp('2013-05-26')])
tempfig.update_layout(xaxis_title="Date", yaxis_title="Temperature (°C) ", legend_title="Location")
tempfig.show()

heatFigLabels = ["Qnet", "Lowpass"]
heatfig = px.line(x = predictedSMidDF['DN'], y = [heatMidDF["Qnet"], outputHeatLow], color_discrete_sequence= ["green", "black"], title = "Heat Flux")
for idx in range(len(heatFigLabels)):
    heatfig.data[idx].name = heatFigLabels[idx]
    heatfig.data[idx].hovertemplate = 'variable=' + heatFigLabels[idx] + '<br>x=%{x}<br>value=%{y}<extra></extra>'
    heatfig.data[idx].legendgroup = heatFigLabels[idx]

heatfig.update_layout(title=dict(text= "Heat Flux for 2013", font=dict(size=25)))
heatfig.update_xaxes(tickangle=30)
heatfig.update_xaxes(rangeslider_visible=True)
heatfig.update_xaxes(range = [pd.Timestamp('2013-01-21'),pd.Timestamp('2013-05-26')])
heatfig.update_layout(xaxis_title="Date", yaxis_title="Heat Flux (W/m2)", legend_title="Location")
heatfig.show()


bottomFigLabels = ['Bottom', 'Predicted', 'Difference','Difference Lowpass']
bottomfig = px.line(x = predictedBMidDF['DN'], y = [predictedBMidDF['OriginalTemp'], predictedBMidDF["ModelTemp"], predictedBMidDF["TempDiff"], outputBottomLow], color_discrete_sequence= ["black", "blue","orange", "red"], title = "Temperature")
for idx in range(len(bottomFigLabels)):
    bottomfig.data[idx].name = bottomFigLabels[idx]
    bottomfig.data[idx].hovertemplate = 'variable=' + bottomFigLabels[idx] + '<br>x=%{x}<br>value=%{y}<extra></extra>'
    bottomfig.data[idx].legendgroup = bottomFigLabels[idx]

bottomfig.update_layout(title=dict(text= "Bottom Temperature Midestuary for 2013", font=dict(size=25)))
bottomfig.update_xaxes(tickangle=30)
bottomfig.update_xaxes(rangeslider_visible=True)
bottomfig.update_xaxes(range = [pd.Timestamp('2013-01-21'),pd.Timestamp('2013-05-26')])
bottomfig.update_layout(xaxis_title="Date", yaxis_title="Temperature (°C) ", legend_title="Location")
bottomfig.show()'''

'\ntempFigLabels = [\'Surface\', \'Predicted\', \'Difference\', \'Difference Lowpass\', \'River Temperature\']\ntempfig = px.line(x = predictedSMidDF[\'DN\'], y = [predictedSMidDF[\'OriginalTemp\'], predictedSMidDF["ModelTemp"], predictedSMidDF[\'TempDiff\'], outputSurfaceLow, riverDF[\'EstimatedTemp\']], color_discrete_sequence= ["black", "blue", "orange", "red", "green"], title = "Temperature")\nfor idx in range(len(tempFigLabels)):\n    tempfig.data[idx].name = tempFigLabels[idx]\n    tempfig.data[idx].hovertemplate = \'variable=\' + tempFigLabels[idx] + \'<br>x=%{x}<br>value=%{y}<extra></extra>\'\n    tempfig.data[idx].legendgroup = tempFigLabels[idx]\n\ntempfig.update_layout(title=dict(text= "Surface Temperature Midestuary for 2013", font=dict(size=25)))\ntempfig.update_xaxes(tickangle=30)\ntempfig.update_xaxes(rangeslider_visible=True)\ntempfig.update_xaxes(range = [pd.Timestamp(\'2013-01-21\'),pd.Timestamp(\'2013-05-26\')])\ntempfig.update_layout(xaxis_title="Date", yaxis_title=